<a href="https://colab.research.google.com/github/Zeaxanthin80/CAI2840C/blob/main/Assignments/Assignment_5_copy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Assignment 5 (Week 4)

## Assignment: Video Processing and Contour Detection Using OpenCV

reference:  https://colab.research.google.com/drive/1_FGt6GyViY1BAK2dIpf5DFjpH79zBV5E?usp=sharingLinks

**Objective:**

In this assignment, you will gain hands-on experience with OpenCV by building three applications in a Google Colab notebook:

1. **Video I/O Application:** Read from and write to a video stream. You can modify or extend the code we used in class.
2. **Motion Detection Application:** Develop a motion detection system that explains the concepts of foreground mass (the difference between the background model and the current frame) and erosion (a morphological operation used to remove noise). You should demonstrate erosion on a new video clip.
3. **Contour Detection Application:** Write code that identifies and draws contours on an image. For extra credit, extend your solution to detect and draw contours in a video (with a clip that is less than one minute long).



---



---



## Part 1: Video I/O Application

**Requirements:**

- **Input:** Use any video file of your choice (or create one, e.g., using your webcam or a synthetic video clip that is less than 1 minute long).
- **Processing:** Implement a simple transformation on each frame (this can be as basic as converting to grayscale, overlaying text, or drawing shapes).
- **Output:** Write the processed frames to a new video file.

**Instructions:**

1. **Reading the Video:**
    - Use cv2.VideoCapture to open the video file.
    - Loop through each frame and perform your processing.
2. **Processing the Frames:**
    - Apply your chosen transformation (for example, add a timestamp overlay or convert to grayscale).
3. **Writing the Video:**
    - Use cv2.VideoWriter to create an output video file.
    - Write the processed frames to this file.

Hint: Ensure your output video settings (frame size, codec, and frame rate) match the input video.

In [16]:
# Cell 1: Opening the Video
    # Opens the video file using cv2.VideoCapture.
    # Checks if the video opened successfully.
    # Gets video properties (width, height, FPS).

import cv2
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

# Path to your video file
video_path = 'https://github.com/Zeaxanthin80/CAI2840C/raw/refs/heads/main/Visuals/bear2.mp4'

# Create a VideoCapture object
cap = cv2.VideoCapture(video_path)

# Check if the video file was successfully opened
if not cap.isOpened():
    print("Error opening video file")
else:
    print("Video file loaded successfully.")

# Get video properties (frame width, height, FPS)
frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps = cap.get(cv2.CAP_PROP_FPS)

print("Frame width:", frame_width)
print("Frame height:", frame_height)
print("FPS:", fps)

Video file loaded successfully.
Frame width: 1280
Frame height: 720
FPS: 25.0


In [17]:
# Cell 1.5: Playback Original Video (using MoviePy)

from moviepy.editor import VideoFileClip
from IPython.display import display

# Download the video file temporarily
import requests
import tempfile

with tempfile.NamedTemporaryFile(suffix=".mp4", delete=False) as temp_file:
    video_data = requests.get(video_path).content
    temp_file.write(video_data)
    temp_file_path = temp_file.name

# Load the video using MoviePy
clip = VideoFileClip(temp_file_path)

# Display the video using ipython_display
clip.ipython_display(width=640, height=360)

Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [18]:
# Cell 2: Processing the Video
  # Creates a cv2.VideoWriter object to write the output video.
  # Enters a loop to read frames from the input video.
  # Converts each frame to grayscale using cv2.cvtColor.
  # Annotates the frame with the FPS using cv2.putText.
  # Writes the processed frame to the output video using out.write.


# Define the codec and create VideoWriter object
fourcc = cv2.VideoWriter_fourcc(*'XVID')  # Use 'XVID' for AVI on Windows
output_video_path = 'output_video.mp4'
out = cv2.VideoWriter(output_video_path, fourcc, fps, (frame_width, frame_height), isColor=True)

# Process the video frame by frame
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break  # Exit loop if no frame is read

    # Processing (optional - replace with your processing logic)
    # gray_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

    # Write the frame to the output video
    out.write(frame)  # or out.write(gray_frame) for grayscale

# Release resources
cap.release()
out.release()
cv2.destroyAllWindows()

print("Video processing and writing completed.")

Video processing and writing completed.


In [19]:
def convert_and_add_fps_single_pass(input_video_path, output_video_path):
    """Converts a video to grayscale and adds FPS overlay in a single pass.

    Args:
        input_video_path: Path to the input video file.
        output_video_path: Path to save the processed video file.
    """
    cap = cv2.VideoCapture(input_video_path)
    if not cap.isOpened():
        print("Error opening video file")
        return

    frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    fps = cap.get(cv2.CAP_PROP_FPS)

    fourcc = cv2.VideoWriter_fourcc(*'XVID')
    out = cv2.VideoWriter(output_video_path, fourcc, fps, (frame_width, frame_height), isColor=False) # isColor=False for grayscale

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # 1. Convert to grayscale
        gray_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

        # 2. Add FPS text to the grayscale frame
        fps_text = f"FPS: {fps:.2f}"
        font = cv2.FONT_HERSHEY_SIMPLEX
        font_scale = 1
        color = (255, 255, 255)  # White color in grayscale (since isColor=False)
        thickness = 2
        (text_width, text_height), _ = cv2.getTextSize(fps_text, font, font_scale, thickness)
        x, y = frame_width - text_width - 10, 10
        cv2.rectangle(gray_frame, (x - 5, y - 5), (x + text_width + 5, y + text_height + 5), (0, 0, 0), -1)  #Black rectangle in grayscale
        cv2.putText(gray_frame, fps_text, (x, y + text_height + 2), font, font_scale, color, thickness)

        # Write the processed frame to the output video
        out.write(gray_frame)



    cap.release()
    out.release()
    print(f"Video processed and saved to: {output_video_path}")

In [20]:
# Set input and output video paths
input_video_path = 'output_video.mp4'
output_video_path = 'processed_output_video.mp4'

# Call the combined function
convert_and_add_fps_single_pass(input_video_path, output_video_path)

Video processed and saved to: processed_output_video.mp4


In [21]:
from moviepy.editor import VideoFileClip

In [22]:
output_video = 'processed_output_video.mp4'
clip = VideoFileClip(output_video)
clip.ipython_display(width = 640)

Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4




---



---



## Part 2: Motion Detection Application with Foreground Mass and Erosion

**Requirements:**

- **Input:** Use a video clip (less than one minute long) that shows some movement.
- **Processing:**
    - Create a **background model** from the initial frames.
    - Compute the **foreground mass** by taking the difference between the current frame and the background model.
    - Apply **erosion** to the foreground mask to remove noise (explain how erosion removes small, isolated noise pixels).
- **Output:** Annotate the frames (e.g., draw bounding boxes around detected motion areas) and write the output to a new video file.

**Instructions:**

1. **Background Modeling & Foreground Mass:**
2. **Applying Erosion:**
3. **Annotation and Video Output:**
    - Draw bounding rectangles (or other markers) around the regions of motion detected in the eroded foreground mask.
    - Write the annotated frames to a new output video.
    
Bonus: You can include intermediate visualizations (e.g., display the raw foreground mask vs. the eroded mask) to show the effect of erosion.



---



## Part 3: Contour Detection Application

**Requirements:**

 - **Input:** Use an image that contains distinct shapes (or create one with simple geometric shapes).
 - **Processing:**
    - Convert the image to grayscale and threshold it to create a binary image.
    - Use cv2.findContours to detect the contours.
    - Use cv2.drawContours to overlay the detected contours on the original image.
- **Output:** Display the resulting image with contours drawn.
- **Bonus:** Extend your code to process a video stream frame-by-frame, drawing contours on each frame.

**Instructions:**

1. **Image Preprocessing:**
    - Load the image and convert it to grayscale.
    - Apply a binary threshold to segment the shapes.
2. **Contour Detection:**
    - Use cv2.findContours with appropriate retrieval and approximation modes.
    - Explain the output: a list of contours and (optionally) a hierarchy that indicates relationships between contours.
3. **Drawing the Contours:**
    - Use cv2.drawContours to overlay the detected contours onto the image.
    - Display the final image.
4. **(Bonus) Video Contour Detection:**
    - Modify your code from Part 1 to process a video.
    - For each frame, detect contours and draw them before writing the frame to an output video file.

Hint: Choose a short video clip (under one minute) to ensure quick processing and review.



---



---



# Playback Video

1. IPython.display.Video:

 * Pros:
     - Simple: Easy to use, just provide the video file path.
     - Native: Integrates well with the notebook environment.
     - Basic Controls: Offers basic playback controls (play, pause, volume).
 * Cons:
     - Limited Functionality: Lacks advanced controls (seeking, frame-by-frame stepping).
     - No Processing: Not suitable for displaying processed video frames directly (you'd need to save the output to a file first).

2. MoviePy:

 * Pros:
     - Flexibility: Provides greater control over playback and manipulation (seeking, trimming, effects).
     - Direct Display: Can display processed video frames directly using clip.ipython_display().
     - More Features: Offers a wider range of video editing and processing capabilities.
 * Cons:
     - More Complex: Requires understanding MoviePy's API and functions.
     - Potential Overhead: Might have some performance overhead compared to IPython.display.Video.

3. Outputting to a File:

 * Pros:
     - Versatility: Works with any video processing library or method.
     - Standard Approach: A common way to share and display processed videos.
     - Compatibility: The output video file can be played in various environments.
 * Cons:
     - Extra Step: Requires saving the processed video to a file before displaying.
     - Storage: Consumes storage space for the output video file.

## **The Best Option**

**For most cases, especially if you're doing video processing, Outputting to a File is generally the best option.**

Here's why:

 - Flexibility: It allows you to use any video processing technique you want with OpenCV or other libraries.
 - Clarity: Separates the processing and display stages, making your code more organized.
 - Sharing: The output video file can be easily shared and viewed outside of the notebook.

When to use the other options:

 - IPython.display.Video: If you just need to quickly display an existing video file without any processing.
 - MoviePy: When you need more control over playback or want to apply basic video editing or effects directly within the notebook.

**In specific scenarios, where you're using OpenCV for video processing, the recommended approach is to:**

1. Process your video using OpenCV.
2. Save the processed frames to a new video file using `cv2.VideoWriter`.
3. Embed or link the output video file in your Colab notebook using `IPython.display.Video` or by providing a download link.

This workflow gives you the most flexibility, clarity, and compatibility for your video processing projects in Colab.